# ICD-9-CM and CUI

### 2023-07-01

ICD-9-CM codes downloaded from https://www.cms.gov/medicare/coordination-benefits-recovery-overview/icd-code-lists

In [14]:
# import data
import pandas as pd

# Read the Excel file
excel_file = r'C:\Users\sungh\icd9cm.xlsx'
icd9cm = pd.read_excel(excel_file)

# Convert to CSV
icd9cmfile = r'C:\Users\sungh\icd9cm.csv'
icd9cm.to_csv(icd9cmfile, index=False)

In [17]:
# Specify the new column names
new_column_names = {'DIAGNOSIS CODE': 'ICD9CM', 'LONG DESCRIPTION': 
                    'Description'}

# Rename the columns in the DataFrame
icd9cm.rename(columns=new_column_names, inplace=True)

#### Drop unnecessary columns:

In [18]:
# Specify the columns to keep
columns_to_keep = ['ICD9CM', 'Description']

# Create a new DataFrame with only the desired columns
icd9cm_updated = icd9cm[columns_to_keep]

# Print the modified DataFrame
print(icd9cm_updated.head(11))

   ICD9CM                                  Description
0    0010               Cholera due to vibrio cholerae
1    0011        Cholera due to vibrio cholerae el tor
2    0019                         Cholera, unspecified
3    0020                                Typhoid fever
4    0021                          Paratyphoid fever A
5    0022                          Paratyphoid fever B
6    0023                          Paratyphoid fever C
7    0029               Paratyphoid fever, unspecified
8    0030                   Salmonella gastroenteritis
9    0031                        Salmonella septicemia
10  00320  Localized salmonella infection, unspecified


### Number of ICD-9 Codes: 

In [19]:
# Count the number of rows
num_rows = len(icd9cm_updated)
print("Number of ICD-9-CM Codes:", num_rows)

Number of ICD-9-CM Codes: 14567


#### Add decimal places to format ICD-9:

In [21]:
def add_decimal(icd_code):
    if len(icd_code) > 3:
        return icd_code[:3] + '.' + icd_code[3:]
    else:
        return icd_code

# Apply the add_decimal function to the 'ICD9' column in your dataframe
icd9cm_updated['ICD9CM_WITH_DECIMAL'] = icd9cm_updated['ICD9CM'].apply(add_decimal)

In [22]:
# Create a new DataFrame without the 'icd9' column
final_icd9cm = icd9cm_updated.drop('ICD9CM', axis=1)

# Verify the new DataFrame
print(final_icd9cm.head())

                             Description ICD9CM_WITH_DECIMAL
0         Cholera due to vibrio cholerae               001.0
1  Cholera due to vibrio cholerae el tor               001.1
2                   Cholera, unspecified               001.9
3                          Typhoid fever               002.0
4                    Paratyphoid fever A               002.1


### From https://documentation.uts.nlm.nih.gov/scripts/crosswalk.py

### 06-27 Update: This code below works (from: https://documentation.uts.nlm.nih.gov/scripts/search-terms.py)

### This step will process the entire data, using "Description" column to produce CSV file that matches CUI: 
#### (will take a while)

In [52]:
import requests
import pandas as pd
from math import ceil

def retrieve_cui(apikey, version, icd_codes, batch_size):
    uri = "https://uts-ws.nlm.nih.gov"
    content_endpoint = "/rest/search/" + version
    full_url = uri + content_endpoint
    result_list = []

    total_batches = ceil(len(icd_codes) / batch_size)

    for batch in range(total_batches):
        start_index = batch * batch_size
        end_index = (batch + 1) * batch_size
        batch_codes = icd_codes[start_index:end_index]

        try:
            for icd_code in batch_codes:
                page = 0  # Reset the page counter for each ICD code
                while True:
                    page += 1
                    query = {'string': icd_code, 'apiKey': apikey, 'pageNumber': page}
                    r = requests.get(full_url, params=query)
                    r.raise_for_status()
                    r.encoding = 'utf-8'
                    outputs = r.json()

                    items = outputs['result']['results']

                    if len(items) == 0:
                        if page == 1:
                            print('No results found for ICD code: ' + icd_code + '\n')
                            break
                        else:
                            break

                    print("Results for ICD code: " + icd_code + ", page " + str(page) + "\n")

                    for result in items:
                        if 'rootSource' in result:
                            cui = result['ui']
                            source_vocab = result['rootSource']
                            print('ICD code: ' + icd_code)
                            print('CUI: ' + cui)
                            print('Source Vocabulary: ' + source_vocab)
                            print('\n')

                            result_dict = {
                                'ICD-9-CM': icd_code,
                                'CUI': cui,
                                'Source Vocabulary': source_vocab
                            }
                            result_list.append(result_dict)

                    print('*********')

        except Exception as except_error:
            print(except_error)

    # Convert the result_list to a DataFrame
    result_df = pd.DataFrame(result_list, columns=['ICD-9-CM', 'CUI', 'Source Vocabulary'])

    # Save the DataFrame to a CSV file
    result_df.to_csv('ICD9CM_CUI_FINAL.csv', index=False)
    print("CSV file saved successfully.")

# Set your UMLS API key and version here
apikey = "49182007-9896-41a5-aae6-f2cb70d0ca5e"
version = "current"

# Replace with your actual ICD codes dataframe
icd_codes = final_icd9cm['ICD9CM_WITH_DECIMAL']
batch_size = 200  # Number of codes to process in each batch

# Call the retrieve_cui function with the provided API key, version, icd_codes, and batch_size
retrieve_cui(apikey, version, icd_codes, batch_size)

Results for ICD code: 001.0, page 1

ICD code: 001.0
CUI: C0008354
Source Vocabulary: MTH


*********
Results for ICD code: 001.1, page 1

ICD code: 001.1
CUI: C0343372
Source Vocabulary: SNOMEDCT_US


*********
Results for ICD code: 001.9, page 1

ICD code: 001.9
CUI: C0008354
Source Vocabulary: MTH


*********
Results for ICD code: 002.0, page 1

ICD code: 002.0
CUI: C0041466
Source Vocabulary: MTH


*********
Results for ICD code: 002.1, page 1

ICD code: 002.1
CUI: C0343375
Source Vocabulary: SNOMEDCT_US


ICD code: 002.1
CUI: C4279561
Source Vocabulary: MSH


*********
Results for ICD code: 002.2, page 1

ICD code: 002.2
CUI: C0343376
Source Vocabulary: SNOMEDCT_US


*********
Results for ICD code: 002.3, page 1

ICD code: 002.3
CUI: C0343377
Source Vocabulary: SNOMEDCT_US


*********
Results for ICD code: 002.9, page 1

ICD code: 002.9
CUI: C0030528
Source Vocabulary: MSH


*********
Results for ICD code: 003.0, page 1

ICD code: 003.0
CUI: C0036114
Source Vocabulary: MTH


*****

Results for ICD code: 008.47, page 1

ICD code: 008.47
CUI: C0374932
Source Vocabulary: ICD9CM


ICD code: 008.47
CUI: C0864584
Source Vocabulary: MEDCIN


*********
Results for ICD code: 008.49, page 1

ICD code: 008.49
CUI: C0489951
Source Vocabulary: MTH


*********
Results for ICD code: 008.5, page 1

ICD code: 008.5
CUI: C0152516
Source Vocabulary: MTH


*********
Results for ICD code: 008.61, page 1

ICD code: 008.61
CUI: C0347854
Source Vocabulary: SNOMEDCT_US


*********
Results for ICD code: 008.62, page 1

ICD code: 008.62
CUI: C0276162
Source Vocabulary: SNOMEDCT_US


*********
Results for ICD code: 008.63, page 1

ICD code: 008.63
CUI: C0374933
Source Vocabulary: MDR


ICD code: 008.63
CUI: C2712971
Source Vocabulary: MTH


ICD code: 008.63
CUI: C0864585
Source Vocabulary: MTHICD9


*********
Results for ICD code: 008.64, page 1

ICD code: 008.64
CUI: C0374934
Source Vocabulary: ICD9CM


*********
Results for ICD code: 008.65, page 1

ICD code: 008.65
CUI: C1611187
Source V

Results for ICD code: 011.32, page 1

ICD code: 011.32
CUI: C0152575
Source Vocabulary: ICD9CM


*********
Results for ICD code: 011.33, page 1

ICD code: 011.33
CUI: C0152576
Source Vocabulary: ICD9CM


*********
Results for ICD code: 011.34, page 1

ICD code: 011.34
CUI: C0152577
Source Vocabulary: ICD9CM


*********
Results for ICD code: 011.35, page 1

ICD code: 011.35
CUI: C0152578
Source Vocabulary: ICD9CM


*********
Results for ICD code: 011.36, page 1

ICD code: 011.36
CUI: C0152579
Source Vocabulary: ICD9CM


*********
Results for ICD code: 011.40, page 1

ICD code: 011.40
CUI: C0041336
Source Vocabulary: SNOMEDCT_US


*********
Results for ICD code: 011.41, page 1

ICD code: 011.41
CUI: C0152580
Source Vocabulary: ICD9CM


*********
Results for ICD code: 011.42, page 1

ICD code: 011.42
CUI: C0152581
Source Vocabulary: ICD9CM


*********
Results for ICD code: 011.43, page 1

ICD code: 011.43
CUI: C0152582
Source Vocabulary: ICD9CM


*********
Results for ICD code: 011.44, pa

Results for ICD code: 012.80, page 1

ICD code: 012.80
CUI: C0152647
Source Vocabulary: ICD9CM


*********
Results for ICD code: 012.81, page 1

ICD code: 012.81
CUI: C0152648
Source Vocabulary: ICD9CM


*********
Results for ICD code: 012.82, page 1

ICD code: 012.82
CUI: C0152649
Source Vocabulary: ICD9CM


*********
Results for ICD code: 012.83, page 1

ICD code: 012.83
CUI: C0152650
Source Vocabulary: ICD9CM


*********
Results for ICD code: 012.84, page 1

ICD code: 012.84
CUI: C0152651
Source Vocabulary: ICD9CM


*********
Results for ICD code: 012.85, page 1

ICD code: 012.85
CUI: C0152652
Source Vocabulary: ICD9CM


*********
Results for ICD code: 012.86, page 1

ICD code: 012.86
CUI: C0152653
Source Vocabulary: ICD9CM


*********
Results for ICD code: 013.00, page 1

ICD code: 013.00
CUI: C0041318
Source Vocabulary: MTH


*********
Results for ICD code: 013.01, page 1

ICD code: 013.01
CUI: C0152655
Source Vocabulary: ICD9CM


*********
Results for ICD code: 013.02, page 1

IC

Results for ICD code: 014.80, page 1

ICD code: 014.80
CUI: C0374962
Source Vocabulary: MTH


*********
Results for ICD code: 014.81, page 1

ICD code: 014.81
CUI: C0152725
Source Vocabulary: ICD9CM


*********
Results for ICD code: 014.82, page 1

ICD code: 014.82
CUI: C0152726
Source Vocabulary: ICD9CM


*********
Results for ICD code: 014.83, page 1

ICD code: 014.83
CUI: C0152727
Source Vocabulary: ICD9CM


*********
Results for ICD code: 014.84, page 1

ICD code: 014.84
CUI: C0152728
Source Vocabulary: ICD9CM


*********
Results for ICD code: 014.85, page 1

ICD code: 014.85
CUI: C0152729
Source Vocabulary: ICD9CM


*********
Results for ICD code: 014.86, page 1

ICD code: 014.86
CUI: C0152730
Source Vocabulary: ICD9CM


*********
Results for ICD code: 015.00, page 1

ICD code: 015.00
CUI: C0041330
Source Vocabulary: MTH


*********
Results for ICD code: 015.01, page 1

ICD code: 015.01
CUI: C0152731
Source Vocabulary: ICD9CM


*********
Results for ICD code: 015.02, page 1

ICD c

...

Results for ICD code: V71.6, page 1

ICD code: V71.6
CUI: C0260871
Source Vocabulary: ICD9CM


ICD code: V71.6
CUI: C2897911
Source Vocabulary: ICD10CM


ICD code: V71.6
CUI: C0868685
Source Vocabulary: MTHICD9


ICD code: V71.6
CUI: C0477062
Source Vocabulary: ICD10


*********
Results for ICD code: V71.7, page 1

ICD code: V71.7
CUI: C0260872
Source Vocabulary: MTH


ICD code: V71.7
CUI: C2897915
Source Vocabulary: ICD10CM


ICD code: V71.7
CUI: C0477063
Source Vocabulary: ICD10


*********
Results for ICD code: V71.81, page 1

ICD code: V71.81
CUI: C0878737
Source Vocabulary: MEDCIN


*********
Results for ICD code: V71.82, page 1

ICD code: V71.82
CUI: C1135309
Source Vocabulary: ICD9CM


*********
Results for ICD code: V71.83, page 1

ICD code: V71.83
CUI: C1135310
Source Vocabulary: ICD9CM


*********
Results for ICD code: V71.89, page 1

ICD code: V71.89
CUI: C0481850
Source Vocabulary: ICD9CM


*********
Results for ICD code: V71.9, page 1

ICD code: V71.9
CUI: C2897919
Source 

Results for ICD code: V74.4, page 1

ICD code: V74.4
CUI: C0260895
Source Vocabulary: ICD9CM


ICD code: V74.4
CUI: C2898011
Source Vocabulary: ICD10CM


ICD code: V74.4
CUI: C0477090
Source Vocabulary: ICD10


*********
Results for ICD code: V74.5, page 1

ICD code: V74.5
CUI: C1955617
Source Vocabulary: MTHICD9


ICD code: V74.5
CUI: C1961127
Source Vocabulary: MTH


ICD code: V74.5
CUI: C2898015
Source Vocabulary: ICD10CM


ICD code: V74.5
CUI: C0477091
Source Vocabulary: ICD10


*********
Results for ICD code: V74.6, page 1

ICD code: V74.6
CUI: C0260897
Source Vocabulary: ICPC2ICD10ENG


ICD code: V74.6
CUI: C2898019
Source Vocabulary: ICD10CM


ICD code: V74.6
CUI: C0477092
Source Vocabulary: ICD10


*********
Results for ICD code: V74.8, page 1

ICD code: V74.8
CUI: C0260898
Source Vocabulary: ICD9CM


ICD code: V74.8
CUI: C0868693
Source Vocabulary: MTHICD9


ICD code: V74.8
CUI: C0868694
Source Vocabulary: MTHICD9


ICD code: V74.8
CUI: C0868696
Source Vocabulary: MTHICD9


IC

Results for ICD code: V77.91, page 1

ICD code: V77.91
CUI: C0878805
Source Vocabulary: MTHICD9


ICD code: V77.91
CUI: C2910614
Source Vocabulary: ICD10CM


ICD code: V77.91
CUI: C0878807
Source Vocabulary: MTH


ICD code: V77.91
CUI: C0878806
Source Vocabulary: MTHICD9


*********
Results for ICD code: V77.99, page 1

ICD code: V77.99
CUI: C0877845
Source Vocabulary: ICD9CM


*********
Results for ICD code: V78.0, page 1

ICD code: V78.0
CUI: C0260935
Source Vocabulary: CHV


ICD code: V78.0
CUI: C2898141
Source Vocabulary: ICD10CM


ICD code: V78.0
CUI: C0477126
Source Vocabulary: ICD10


*********
Results for ICD code: V78.1, page 1

ICD code: V78.1
CUI: C0260936
Source Vocabulary: ICD9CM


ICD code: V78.1
CUI: C2898145
Source Vocabulary: ICD10CM


ICD code: V78.1
CUI: C0477127
Source Vocabulary: ICD10


*********
Results for ICD code: V78.2, page 1

ICD code: V78.2
CUI: C0260937
Source Vocabulary: MTH


ICD code: V78.2
CUI: C2898149
Source Vocabulary: ICD10CM


ICD code: V78.2
CUI

Results for ICD code: V84.81, page 1

ICD code: V84.81
CUI: C1955618
Source Vocabulary: ICD10CM


*********
Results for ICD code: V84.89, page 1

ICD code: V84.89
CUI: C1455996
Source Vocabulary: MTH


*********
Results for ICD code: V85.0, page 1

ICD code: V85.0
CUI: C0477197
Source Vocabulary: ICD10


ICD code: V85.0
CUI: C1561710
Source Vocabulary: ICD9CM


*********
Results for ICD code: V85.1, page 1

ICD code: V85.1
CUI: C0477198
Source Vocabulary: ICD10


ICD code: V85.1
CUI: C1561711
Source Vocabulary: ICD9CM


*********
Results for ICD code: V85.21, page 1

ICD code: V85.21
CUI: C2911045
Source Vocabulary: ICD10CM


*********
Results for ICD code: V85.22, page 1

ICD code: V85.22
CUI: C2911046
Source Vocabulary: ICD10CM


*********
Results for ICD code: V85.23, page 1

ICD code: V85.23
CUI: C2911047
Source Vocabulary: ICD10CM


*********
Results for ICD code: V85.24, page 1

ICD code: V85.24
CUI: C2911048
Source Vocabulary: ICD10CM


*********
Results for ICD code: V85.25, pa

Results for ICD code: V90.10, page 1

ICD code: V90.10
CUI: C2898917
Source Vocabulary: ICD10CM


ICD code: V90.10
CUI: C2921327
Source Vocabulary: ICD10CM


*********
Results for ICD code: V90.11, page 1

ICD code: V90.11
CUI: C2898921
Source Vocabulary: ICD10CM


ICD code: V90.11
CUI: C2898923
Source Vocabulary: ICD10CM


ICD code: V90.11
CUI: C2921328
Source Vocabulary: ICD10CM


ICD code: V90.11
CUI: C2898922
Source Vocabulary: ICD10CM


*********
Results for ICD code: V90.12, page 1

ICD code: V90.12
CUI: C2898927
Source Vocabulary: ICD10CM


ICD code: V90.12
CUI: C2921329
Source Vocabulary: ICD10CM


*********
Results for ICD code: V90.2, page 1

ICD code: V90.2
CUI: C2921331
Source Vocabulary: MTHICD9


ICD code: V90.2
CUI: C2921330
Source Vocabulary: MTHICD9


ICD code: V90.2
CUI: C2921332
Source Vocabulary: MTHICD9


ICD code: V90.2
CUI: C2921333
Source Vocabulary: ICD10CM


ICD code: V90.2
CUI: C2899003
Source Vocabulary: ICD10CM


ICD code: V90.2
CUI: C0477245
Source Vocabul